# Feature Engineering

The next step is to create features from the raw text so we can train the machine learning models. The steps followed are:

1. **Text Cleaning and Preparation**: cleaning of special characters, downcasing, punctuation signs. possessive pronouns and stop words removal and lemmatization. 
2. **Label coding**: creation of a dictionary to map each category to a code.
3. **Train-test split**: to test the models on unseen data.
4. **Text representation**: use of TF-IDF scores to represent text.

In [1]:
import pickle
import pandas as pd
import re
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.feature_selection import chi2
import numpy as np

First of all we'll load the dataset:

In [2]:
#path_df = "/home/lnc/0. Latest News Classifier/02. Exploratory Data Analysis/News_dataset.pickle"

#with open(path_df, 'rb') as data:
#    df = pickle.load(data)

In [3]:
df = pd.read_csv('ml_model.csv')

C:\Users\Sarah\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3049: DtypeWarning: Columns (0,1,2,12,13) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


And visualize one sample news content:

In [4]:
df = df.drop(df.index[21932:42286])

Finally, we can delete the intermediate columns:

In [5]:
print(df.columns)

Index(['Name', 'Type', 'Party', 'Republican', 'year', 'mean_word_length',
       'word_count', 'some_word_count', 'unique_word', 'some_unique_word',
       'unique_word_ratio', 'some_unique_word_ratio', 'words', 'sentences',
       'mean_sentence_length', 'positive_words', 'negative_words',
       'positive_words_ratio', 'negative_words_ratio', 'we_count', 'war_count',
       'i_count', 'Sentences', 'vader_neg', 'vader_pos', 'vader_neu',
       'vader_com'],
      dtype='object')


In [6]:
#df.head(1)
df.drop(['year','we_count','war_count','i_count','words'], axis=1, inplace=True)

In [7]:
print(df.columns)

Index(['Name', 'Type', 'Party', 'Republican', 'mean_word_length', 'word_count',
       'some_word_count', 'unique_word', 'some_unique_word',
       'unique_word_ratio', 'some_unique_word_ratio', 'sentences',
       'mean_sentence_length', 'positive_words', 'negative_words',
       'positive_words_ratio', 'negative_words_ratio', 'Sentences',
       'vader_neg', 'vader_pos', 'vader_neu', 'vader_com'],
      dtype='object')


In [9]:
list_columns = ['Name', 'Type', 'Party', 'Republican', 'mean_word_length', 'word_count',
       'some_word_count', 'unique_word', 'some_unique_word',
       'unique_word_ratio', 'some_unique_word_ratio', 'sentences',
       'mean_sentence_length', 'positive_words', 'negative_words',
       'positive_words_ratio', 'negative_words_ratio', 'Sentences', 'vader_neg', 
        'vader_pos', 'vader_neu', 'vader_com']
df = df[list_columns]

df = df.rename(columns={'Sentences': 'Sentences'})

In [11]:
print(df.shape)
print(df.columns)

(21932, 22)
Index(['Name', 'Type', 'Party', 'Republican', 'mean_word_length', 'word_count',
       'some_word_count', 'unique_word', 'some_unique_word',
       'unique_word_ratio', 'some_unique_word_ratio', 'sentences',
       'mean_sentence_length', 'positive_words', 'negative_words',
       'positive_words_ratio', 'negative_words_ratio', 'Sentences',
       'vader_neg', 'vader_pos', 'vader_neu', 'vader_com'],
      dtype='object')


**IMPORTANT:**

We need to remember that our model will gather the latest news articles from different newspapers every time we want. For that reason, we not only need to take into account the peculiarities of the training set articles, but also possible ones that are present in the gathered news articles.

For this reason, possible peculiarities have been studied in the *05. News Scraping* folder.

## 2. Label coding

We'll create a dictionary with the label codification:

In [12]:
category_codes = {
    'Democrat': 0,
    'Republican': 1}

In [13]:
# Category mapping
df['Republican'] = df['Party']
df = df.replace({'Republican':category_codes})

In [14]:
df.head()

Name                Type       Party  Republican  mean_word_length  \
0  Donald Trump  State of the Union  Republican           1           6.01407   
1  Donald Trump  State of the Union  Republican           1           6.01407   
2  Donald Trump  State of the Union  Republican           1           6.01407   
3  Donald Trump  State of the Union  Republican           1           6.01407   
4  Donald Trump  State of the Union  Republican           1           6.01407   

   word_count  some_word_count  unique_word  some_unique_word  \
0     29897.0          22255.0       1659.0            1387.0   
1     29897.0          22255.0       1659.0            1387.0   
2     29897.0          22255.0       1659.0            1387.0   
3     29897.0          22255.0       1659.0            1387.0   
4     29897.0          22255.0       1659.0            1387.0   

   unique_word_ratio  ...  mean_sentence_length positive_words  \
0           0.055491  ...            105.414634          244.0   
1           0.055491  ...            105.414634          244.0   
2           0.055491  ...            105.414634          244.0   
3           0.055491  ...            105.414634          244.0   
4           0.055491  ...            105.414634          244.0   

   negative_words  positive_words_ratio  negative_words_ratio  \
0           177.0              0.010964              0.007953   
1           177.0              0.010964              0.007953   
2           177.0              0.010964              0.007953   
3           177.0              0.010964              0.007953   
4           177.0              0.010964              0.007953   

                                           Sentences  vader_neg vader_pos  \
0        madam speaker, mr. vice president, membe...      0.000     0.097   
1  as we begin a new congress, i stand here ready...      0.000     0.122   
2  millions of our fellow citizens are watching u...      0.053     0.159   
3  the agenda i will lay out this evening is not ...      0.000     0.000   
4           it is the agenda of the american people.      0.000     0.000   

   vader_neu  vader_com  
0      0.903     0.4215  
1      0.878     0.3612  
2      0.788     0.4954  
3      1.000     0.0000  
4      1.000     0.0000  

[5 rows x 22 columns]

## 3. Train - test split

We'll set apart a test set to prove the quality of our models. We'll do Cross Validation in the train set in order to tune the hyperparameters and then test performance on the unseen data of the test set.

In [15]:
X_train, X_test, y_train, y_test = train_test_split(df['Sentences'], 
                                                    df['Republican'], 
                                                    test_size=0.30, 
                                                    random_state=8)

Since we relatively many observations (21.932), we'll choose a test set size of 30% of the full dataset.

## 4. Text representation

We have various options:

* Count Vectors as features
* TF-IDF Vectors as features
* Word Embeddings as features
* Text / NLP based features
* Topic Models as features

We'll use **TF-IDF Vectors** as features.

We have to define the different parameters:

* `ngram_range`: We want to consider both unigrams and bigrams.
* `max_df`: When building the vocabulary ignore terms that have a document
    frequency strictly higher than the given threshold
* `min_df`: When building the vocabulary ignore terms that have a document
    frequency strictly lower than the given threshold.
* `max_features`: If not None, build a vocabulary that only consider the top
    max_features ordered by term frequency across the corpus.

See `TfidfVectorizer?` for further detail.

It needs to be mentioned that we are implicitly scaling our data when representing it as TF-IDF features with the argument `norm`.

In [16]:
# Parameter election
ngram_range = (1,2)
min_df = 10
max_df = 1.
max_features = 22

We have chosen these values as a first approximation. Since the models that we develop later have a very good predictive power, we'll stick to these values. But it has to be mentioned that different combinations could be tried in order to improve even more the accuracy of the models.

In [17]:
tfidf = TfidfVectorizer(encoding='utf-8',
                        ngram_range=ngram_range,
                        stop_words=None,
                        lowercase=False,
                        max_df=max_df,
                        min_df=min_df,
                        max_features=max_features,
                        norm='l2',
                        sublinear_tf=True)
                        
features_train = tfidf.fit_transform(X_train).toarray()
labels_train = y_train
print(features_train.shape)

features_test = tfidf.transform(X_test).toarray()
labels_test = y_test
print(features_test.shape)

(15352, 22)
(6580, 22)


Please note that we have fitted and then transformed the training set, but we have **only transformed** the **test set**.

We can use the Chi squared test in order to see what unigrams and bigrams are most correlated with each category:

In [18]:
from sklearn.feature_selection import chi2
import numpy as np

for speech, party in sorted(df['Republican'].items()):
    features_chi2 = chi2(features_train, labels_train == party)
    indices = np.argsort(features_chi2[0])
    feature_names = np.array(tfidf.get_feature_names())[indices]
    unigrams = [v for v in feature_names if len(v.split(' ')) == 1]
    bigrams = [v for v in feature_names if len(v.split(' ')) == 2]
    print("# '{}' category:".format(speech))
    print("  . Most correlated unigrams:\n. {}".format('\n. '.join(unigrams[-5:])))
    print("  . Most correlated bigrams:\n. {}".format('\n. '.join(bigrams[-2:])))
    print("")


# '0' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '1' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '2' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '3' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '4' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '5' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '6' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '7' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '8' category:
  . Most

  . Most correlated bigrams:
. in the
. of the

# '68' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '69' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '70' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '71' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '72' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '73' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '74' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '75' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correla

# '145' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '146' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '147' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '148' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '149' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '150' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '151' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '152' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '153' 

# '212' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '213' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '214' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '215' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '216' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '217' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '218' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '219' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '220' 

# '283' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '284' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '285' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '286' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '287' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '288' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '289' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '290' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '291' 

...

# '21564' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21565' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21566' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21567' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21568' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21569' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21570' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21571' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. 

# '21639' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21640' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21641' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21642' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21643' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21644' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21645' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21646' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. 

  . Most correlated bigrams:
. in the
. of the

# '21714' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21715' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21716' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21717' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21718' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21719' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21720' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21721' category:
  . Most correlated unigrams:
. is
. the
. that
. 

# '21788' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21789' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21790' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21791' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21792' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21793' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21794' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21795' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. 

# '21861' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21862' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21863' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21864' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21865' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21866' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21867' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. of the

# '21868' category:
  . Most correlated unigrams:
. is
. the
. that
. we
. of
  . Most correlated bigrams:
. in the
. 

As we can see, the unigrams correspond well to their category. However, bigrams do not. If we get the bigrams in our features:

In [19]:
bigrams

['in the', 'of the']

We can see there are only six. This means the unigrams have more correlation with the category than the bigrams, and since we're restricting the number of features to the most representative 300, only a few bigrams are being considered.

Let's save the files we'll need in the next steps:

In [20]:
# X_train
with open('Pickles/X_train.pickle', 'wb') as output:
    pickle.dump(X_train, output)
    
# X_test    
with open('Pickles/X_test.pickle', 'wb') as output:
    pickle.dump(X_test, output)
    
# y_train
with open('Pickles/y_train.pickle', 'wb') as output:
    pickle.dump(y_train, output)
    
# y_test
with open('Pickles/y_test.pickle', 'wb') as output:
    pickle.dump(y_test, output)
    
# df
with open('Pickles/df.pickle', 'wb') as output:
    pickle.dump(df, output)
    
# features_train
with open('Pickles/features_train.pickle', 'wb') as output:
    pickle.dump(features_train, output)

# labels_train
with open('Pickles/labels_train.pickle', 'wb') as output:
    pickle.dump(labels_train, output)

# features_test
with open('Pickles/features_test.pickle', 'wb') as output:
    pickle.dump(features_test, output)

# labels_test
with open('Pickles/labels_test.pickle', 'wb') as output:
    pickle.dump(labels_test, output)
    
# TF-IDF object
with open('Pickles/tfidf.pickle', 'wb') as output:
    pickle.dump(tfidf, output)